In [10]:
import pandas as pd
from gensim import models, corpora
from gensim.parsing.preprocessing import preprocess_string, strip_tags, strip_punctuation
from gensim.parsing.preprocessing import remove_stopwords, stem_text, strip_non_alphanum, strip_multiple_whitespaces
from gensim.parsing.preprocessing import strip_short, strip_numeric
from gensim.parsing.preprocessing import STOPWORDS
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
import multiprocessing as mp
import nltk
import pandas as pd
import numpy as np
import tensorflow as tf
from scipy import spatial
import parmap
import os
import swifter
from tqdm import tqdm
import sqlite3

In [11]:
topics_index_to_name_map = {
    0: 'Agriculture, animals, food and rural affairs',
    1: 'Asylum, immigration and nationality',
    2: 'Business, industry and consumers',
    3: 'Communities and families',
    4: 'Crime, civil law, justice and rights',
    5: 'Culture, media and sport',
    6: 'Defence',
    7: 'Economy and finance',
    8: 'Education',
    9: 'Employment and training',
    10: 'Energy and environment',
    11: 'European Union',
    12: 'Health services and medicine',
    13: 'Housing and planning',
    14: 'International affairs',
    15: 'Parliament, government and politics',
    16: 'Science and technology',
    17: 'Social security and pensions',
    18: 'Social services',
    19: 'Transport',
    20: 'Others'
}
topics_name_to_index_map = {y:x for x,y in topics_index_to_name_map.items()}

def strip_short2(text):
    return strip_short(text, minsize=4)


def preprocess_text(text):
    FILTERS = [lambda x: x.lower(), strip_multiple_whitespaces, strip_tags, strip_punctuation,
                   strip_non_alphanum, strip_numeric, strip_short2]
    return preprocess_string(text, FILTERS)

def preprocess(topic):
    ret = []
    topic = topic.strip()
    
    if '|' in topic:
        topics = topic.split('|')
        t = topics[0]
        t = t.strip()
        return topics_name_to_index_map[t]
        
    return topics_name_to_index_map[topic]

In [12]:
df = pd.read_csv('../data/partitions/bert_partitions_54_2017.csv')
df = df.drop(['Source', 'Program Name', 'Time'], axis=1)


In [13]:
df['Date'] = pd.to_datetime(df['Date'])

In [14]:
df

Unnamed: 0       Date  Duration  \
0              0 2017-09-02  235 mins   
1              1 2017-09-02   15 mins   
2              2 2017-09-02   10 mins   
3              3 2017-09-02    5 mins   
4              4 2017-09-02   20 mins   
...          ...        ...       ...   
2086        2086 2017-12-18   30 mins   
2087        2087 2017-12-18   15 mins   
2088        2088 2017-12-18   30 mins   
2089        2089 2017-12-18   30 mins   
2090        2090 2017-12-18   15 mins   

                                             Transcript  \
0     and she paid a price for it. # ..Love you... #...   
1     Went down to London on my own. It was very, ve...   
2     # We can kiss the sky... # Feel the Strictly e...   
3     this afternoon Italy - by securing his 69th po...   
4     # You sexy thing # Where did you come from, ba...   
...                                                 ...   
2086  Well, well. 2m Family films for a Christmas to...   
2087  for English cricket. To lose the Ashes after t...   
2088  No more secrets. You’re reading my mind now. W...   
2089  Ho-ho-ho! Merry Christmas! Yes! I want to give...   
2090  to live to at least 100. That’s around 8.5 mil...   

                                 partitioned_transcript  
0     # ..Love you... # 0n the front line of Britain...  
1     Everybody that had a backpack, "Have they got ...  
2     # We can kiss the sky... # Feel the Strictly e...  
3     this afternoon Italy - by securing his 69th po...  
4     # You sexy thing # Where did you come from, ba...  
...                                                 ...  
2086  2m Family films for a Christmas together on BB...  
2087  To lose the Ashes after three matches will be ...  
2088  Tonight at six, a damning report says Bristol’...  
2089  Tonight at Ten: President Trump outlines a new...  
2090  So how should we prepare for what’s being call...  

[2091 rows x 5 columns]

In [15]:
doc2vec_model = Doc2Vec.load('../models/doc2vec/doc2vec_news_2017_no_Others')

In [16]:
partitions = []
for index, row in df.iterrows():
    partition_string = row['partitioned_transcript']
    partition_date = row['Date']
    all_partitions = partition_string.split('\n---------------------\n')
    for partition in all_partitions:
        partitions.append((index, partition_date, partition))
partition_df = pd.DataFrame(partitions, columns=['partition_id', 'date', 'transcript'])

In [17]:
mask = (partition_df['date'] >= '2017-1-1') & (partition_df['date'] <= '2017-6-30')
partition_df = partition_df.loc[mask]

In [18]:
partition_df

partition_id       date  \
12756            197 2017-05-01   
12757            197 2017-05-01   
12758            197 2017-05-01   
12759            197 2017-05-01   
12760            197 2017-05-01   
...              ...        ...   
104763          1494 2017-03-31   
104764          1494 2017-03-31   
104765          1494 2017-03-31   
104766          1494 2017-03-31   
104767          1494 2017-03-31   

                                               transcript  
12756   MasterChef Semifinals... MasterChef Ser galler...  
12757   A chance discovery by a pre-school child has s...  
12758   As Australia tightens up its visa rules for sk...  
12759   And before we go, let’s take you to Chengdu Ci...  
12760   And I think we will keep similar contrast thro...  
...                                                   ...  
104763  The Flying Scotsman was back on one of Britain...  
104764  lshould warn you Danny Savage’s report contain...  
104765  One of the most famous names in the world of s...  
104766  Now on BBC One, it’s time for the news where y...  
104767  A self-styled Nigerian bishop and a female chu...  

[64688 rows x 3 columns]

In [19]:
partition_df['vector'] = partition_df.swifter.apply(lambda x: doc2vec_model.infer_vector(preprocess_text(x['transcript'])), axis=1)

In [20]:
del df

In [21]:
articles = pd.read_csv('../data/news_predictions/news_2017_predictions.csv')

In [22]:
articles = articles.dropna(subset=['transcript'])
articles = articles.loc[articles.top1_topic != 'Others']

In [23]:
articles = articles.drop(['Unnamed: 0'], axis=1)
articles = articles.loc[articles.month.isin([1,2,3,4,5,6])]
articles

source_id             source  day  month  year  \
0          400553  Belfast Telegraph    1      1  2017   
2          400553  Belfast Telegraph    1      1  2017   
3          400553  Belfast Telegraph    1      1  2017   
4          400553  Belfast Telegraph    1      1  2017   
5          400553  Belfast Telegraph    1      1  2017   
...           ...                ...  ...    ...   ...   
823125     412338              Wales   30      6  2017   
823126     412338              Wales   30      6  2017   
823127     412338              Wales   30      6  2017   
823129     412338              Wales   30      6  2017   
823130     412338              Wales   30      6  2017   

                                             program_name  \
0       Yaya Toure reveals Pep Guardiola's anger at Ma...   
2       Stoke manager Mark Hughes hails Peter Crouch's...   
3       David Moyes braced for "difficult" January win...   
4       Georginio Wijnaldum unfazed by Chelsea's winni...   
5       Sherlock fans shocked after Mary Watson killed...   
...                                                   ...   
823125  Lions dressing room reveal Warren Gatland's cr...   
823126  Idriss Saadi to be given the chance to impress...   
823127  Children in Vietnam gave this amazing renditio...   
823129  999 turns 80 years old - the most ridiculous e...   
823130  A new bullying film made in Wales is hoped to ...   

                                               transcript  parliament  \
0       A lacklustre City lost 1-0 at second-placed Li...           1   
2       Crouch netted in Stoke's 4-2 loss at Chelsea a...           1   
3       For the second straight season the Black Cats ...           1   
4       A 13th successive victory, tying Arsenal's eff...           1   
5       The character, played by Amanda Abbington, die...           1   
...                                                   ...         ...   
823125  The Kiwi has often used it as a tactic to get ...           1   
823126  But a summer exit for the Algeria internationa...           1   
823127  And the words were displayed phonetically on a...           1   
823129  The last eight decades have seen the service e...           1   
823130  The Firehorse Productions movie will have its ...           1   

                                  top1_topic  top1_acc  \
0                   Culture, media and sport     96.34   
2       Crime, civil law, justice and rights     22.13   
3           Business, industry and consumers     29.02   
4                   Culture, media and sport     97.40   
5                   Culture, media and sport     87.56   
...                                      ...       ...   
823125              Culture, media and sport     35.33   
823126              Culture, media and sport     32.85   
823127   Parliament, government and politics     24.29   
823129              Culture, media and sport     49.40   
823130                             Education     32.19   

                                  top2_topic  top2_acc  \
0       Crime, civil law, justice and rights      0.79   
2        Parliament, government and politics     21.14   
3                                     Others     21.56   
4                                     Others      0.69   
5                                     Others      7.63   
...                                      ...       ...   
823125                             Transport     18.68   
823126                                Others     17.47   
823127              Culture, media and sport     21.36   
823129                                Others     12.63   
823130                                Others     17.42   

                              top3_topic  top3_acc  
0       Business, industry and consumers      0.75  
2               Culture, media and sport     20.00  
3               Culture, media and sport     11.25  
4                              Education      0.58  
5               Communities and families  

In [24]:
vector = []
transcripts = articles.transcript.values

preprocessed_transcripts = parmap.map(preprocess_text, transcripts, pm_pbar=True)

587264it [01:10, 8300.59it/s]                             


In [25]:
vector_transcripts = parmap.map(doc2vec_model.infer_vector, preprocessed_transcripts, pm_pbar=True)
articles['vector'] = vector_transcripts

587264it [08:49, 1110.01it/s]                            


In [26]:
del preprocessed_transcripts
# del articles

In [27]:
articles

source_id             source  day  month  year  \
0          400553  Belfast Telegraph    1      1  2017   
2          400553  Belfast Telegraph    1      1  2017   
3          400553  Belfast Telegraph    1      1  2017   
4          400553  Belfast Telegraph    1      1  2017   
5          400553  Belfast Telegraph    1      1  2017   
...           ...                ...  ...    ...   ...   
823125     412338              Wales   30      6  2017   
823126     412338              Wales   30      6  2017   
823127     412338              Wales   30      6  2017   
823129     412338              Wales   30      6  2017   
823130     412338              Wales   30      6  2017   

                                             program_name  \
0       Yaya Toure reveals Pep Guardiola's anger at Ma...   
2       Stoke manager Mark Hughes hails Peter Crouch's...   
3       David Moyes braced for "difficult" January win...   
4       Georginio Wijnaldum unfazed by Chelsea's winni...   
5       Sherlock fans shocked after Mary Watson killed...   
...                                                   ...   
823125  Lions dressing room reveal Warren Gatland's cr...   
823126  Idriss Saadi to be given the chance to impress...   
823127  Children in Vietnam gave this amazing renditio...   
823129  999 turns 80 years old - the most ridiculous e...   
823130  A new bullying film made in Wales is hoped to ...   

                                               transcript  parliament  \
0       A lacklustre City lost 1-0 at second-placed Li...           1   
2       Crouch netted in Stoke's 4-2 loss at Chelsea a...           1   
3       For the second straight season the Black Cats ...           1   
4       A 13th successive victory, tying Arsenal's eff...           1   
5       The character, played by Amanda Abbington, die...           1   
...                                                   ...         ...   
823125  The Kiwi has often used it as a tactic to get ...           1   
823126  But a summer exit for the Algeria internationa...           1   
823127  And the words were displayed phonetically on a...           1   
823129  The last eight decades have seen the service e...           1   
823130  The Firehorse Productions movie will have its ...           1   

                                  top1_topic  top1_acc  \
0                   Culture, media and sport     96.34   
2       Crime, civil law, justice and rights     22.13   
3           Business, industry and consumers     29.02   
4                   Culture, media and sport     97.40   
5                   Culture, media and sport     87.56   
...                                      ...       ...   
823125              Culture, media and sport     35.33   
823126              Culture, media and sport     32.85   
823127   Parliament, government and politics     24.29   
823129              Culture, media and sport     49.40   
823130                             Education     32.19   

                                  top2_topic  top2_acc  \
0       Crime, civil law, justice and rights      0.79   
2        Parliament, government and politics     21.14   
3                                     Others     21.56   
4                                     Others      0.69   
5                                     Others      7.63   
...                                      ...       ...   
823125                             Transport     18.68   
823126                                Others     17.47   
823127              Culture, media and sport     21.36   
823129                                Others     12.63   
823130                                Others     17.42   

                              top3_topic  top3_acc  \
0       Business, industry and consumers      0.75   
2               Culture, media and sport     20.00   
3               Culture, media and sport     11.25   
4                              Education      0.58   
5               Communities and famil

In [28]:
#articles.to_csv('./data/news_2016_predictions_vectored.csv')

In [29]:
import datetime
articles['date'] = articles.apply(lambda x: datetime.date(x.year, x.month, x.day), axis=1)

In [ ]:
# articles = articles.drop(['day', 'month', 'year'], axis=1)

In [ ]:
#articles['vector'] = articles.vector.apply(lambda x: list(x))

In [ ]:
# sample = partition_df.sample(n=1000, weights='partition_id', random_state=1).reset_index(drop=True)

In [ ]:
# def smoothing(df):
#     n = len(df)
#     rows = []
#     for i in tqdm(range(n-1)):
#         row1 = df.iloc[i]
#         row2 = df.iloc[i+1]
#         dt = row1.date
#         start_dt = dt - timedelta(days=2)
#         end_dt = dt + timedelta(days=2)
#         articles_window = articles.loc[(articles['date'] >= start_dt) & (articles['date'] <= end_dt)]
#         row1_vector = np.array(row1.vector)
#         row1_vector = row1_vector.reshape(1, 100)
#         articles_vector = articles_window.vector.values
#         vec = [articles_vector[i] for i in range(len(articles_vector))]
#         vec = np.array(vec)
#         sim = cosine_similarity(row1_vector, vec)[0]
#         max_index = np.argmax(sim)
#         topic1 = articles_window.iloc[max_index]['top1_topic']
        
#         combined_transcript = row1.transcript + ' ' + row2.transcript
#         combined_vector = doc2vec_model.infer_vector(preprocess_text(combined_transcript))
#         combined_vector = np.array(combined_vector)
#         combined_vector = combined_vector.reshape(1, 100)
        
#         combined_sim = cosine_similarity(combined_vector, vec)[0]
#         max_index = np.argmax(combined_sim)
#         topic2 = articles_window.iloc[max_index]['top1_topic']
        
#         row = [row1.partition_id, row1.date, row1.transcript, max(sim), topic1, max(combined_sim), topic2]
#         rows.append(row)
    
#     columns = ['partition_id', 'date', 'transcript', 'similarity', 'topic', 'merged_similarity', 'merged_topic']
#     res_df = pd.DataFrame(rows, columns=columns)
#     return res_df

# res_df = smoothing(partition_df)
# res_df.to_csv('partition_similarity_with_merging_June_21-25_2016.csv')
# res_df

In [30]:
from sklearn.metrics.pairwise import cosine_similarity
from datetime import datetime, timedelta

In [31]:
def predict(partition):
    dt = partition.date
    start_dt = dt - timedelta(days=2)
    end_dt = dt + timedelta(days=2)
    articles_window = articles.loc[(articles['date'] >= start_dt) & (articles['date'] <= end_dt)]
    print(len(articles_window))
    partition_vector = np.array(partition.vector)
    partition_vector = partition_vector.reshape(1, 100)
    articles_vector = articles_window.vector.values
    vec = [articles_vector[i] for i in range(len(articles_vector))]
    vec = np.array(vec)
    sim = cosine_similarity(partition_vector, vec)
    max_index = np.argmax(sim)
    
    return articles_window.iloc[max_index]['top1_topic']

def predict_with_bert(partition):
    dt = partition.date
    start_dt = dt - timedelta(days=2)
    end_dt = dt + timedelta(days=2)
    articles_window = articles.loc[(articles['date'] >= start_dt) & (articles['date'] <= end_dt)]
    partition_transcript = np.array(partition.transcript)
    articles_transcript = articles_window.transcript.values
    input_data = [(partition_transcript, a) for a in articles_transcript]
    print(input_data[0])
    sim = web_model.predict(input_data)
    max_index = np.argmax(sim)
    
    return articles_window.iloc[max_index]['top1_topic']


In [32]:
predict(partition_df.iloc[4])

14782


'Energy and environment'

In [33]:
partition_df.iloc[4].transcript

'And I think we will keep similar contrast through bank holiday Monday, because this area of low pressure is parked across the south of the UK. But here will see some of the highest into the afternoon. We might see one or two early showers in northern England, but they tend to fade away. Generally speaking, northern England and northwards will be dry, bright, and breezy. The southern half of the UK will see cloud and outbreaks of rain, possibly some showers. Could go as high as 18 in the sunshine on the western side. Now, through the evening, those showers could be heavy and thundery across that central sway of England, working ever southwards, eventually clearing away. A fair bit of low cloud coming into that eastern side of the UK. Temperatures at about seven, eight, or nine degrees in major cities. Through Tuesday, the low pressure system will drift to the south, allowing a low pressure system in Scandinavia to become the driving force of our weather. And that will be with us fora g

In [34]:
partition_df.iloc[4]

partition_id                                                  197
date                                          2017-05-01 00:00:00
transcript      And I think we will keep similar contrast thro...
vector          [-0.11908019, -0.5211031, -1.646922, -0.322605...
Name: 12760, dtype: object

In [ ]:
preds = []

for index, row in tqdm(partition_df.iterrows(), total=len(partition_df)):
    preds.append(predict(row))
    
partition_df['prediction'] = preds


  0%|          | 1/64688 [00:01<19:01:48,  1.06s/it]

14782


  0%|          | 2/64688 [00:01<16:51:53,  1.07it/s]

14782


  0%|          | 3/64688 [00:02<14:37:35,  1.23it/s]

...

15637


 51%|█████     | 32775/64688 [3:31:07<3:17:00,  2.70it/s]

15637


 51%|█████     | 32776/64688 [3:31:07<3:17:37,  2.69it/s]

15637


In [ ]:
partition_df

In [ ]:
partition_df.to_csv('./window_topic_predictions_Jan-June_2017.csv')